In [2]:
import os
import pickle
import math
import h5py
import pandas as pd
import shutil
import plotly.express as px
import plotly.graph_objects as go
from osbrain import run_nameserver
from osbrain import run_agent
import numpy as np
import time

import src.utils.performance_measure as pm
import src.bb.blackboard_optimization as bb_opt
import src.controller as controller
from src.ka.ka_s.pymoo_plugin import PyMooAlgorithm
from src.ka.ka_brs.level3 import KaBrLevel3
from src.ka.ka_brs.level2 import KaBrLevel2
from src.ka.ka_brs.level1 import KaBrLevel1
from src.ka.ka_s.stochastic import Stochastic
from src.ka.ka_s.latin_hypercube import LatinHypercube
from src.ka.ka_s.neighborhood_search import NeighborhoodSearch
from src.ka.ka_s.hill_climb import HillClimb
from src.ka.ka_s.genetic_algorithm import GeneticAlgorithm
from src.utils.problem import SFRProblem




In [3]:
design_variables = {'height':     {'ll': 50.0, 'ul': 100.0, 'variable type': float},
                    'smear':      {'ll': 50.0, 'ul': 80.0, 'variable type': float},
                    'pu_content': {'ll': 0.0,  'ul': 1.0,  'variable type': float}}
# Divide Rx swing into 10 pcm 
# Divide burnup in 1 MT/GWd 
full_div = {'reactivity swing': 300, 'burnup':300, 'pu mass': 250, 'pu ratio': 200, 'pu disposed': 100}

kas_sa = {'ka_rp_explore': {'type': Stochastic, 'attr' : {}}, 
       'ka_rp_lhc': {'type': LatinHypercube, 'attr' : {'samples': len(design_variables)*50}},
       'ka_rp_hc': {'type': HillClimb, 'attr' : {'hc_type':'steepest ascent','step_limit':25}},
       'ka_rp_pert': {'type': NeighborhoodSearch, 'attr' : {'neighboorhood_search':'random'}},
       'ka_rp_ga': {'type': GeneticAlgorithm, 'attr' : {}},
       'ka_rp_pymoo': {'type': PyMooAlgorithm, 'attr' : {'pop_size': 40, 'n_offspring': 40, 'termination_criteria':800, '_base_trigger_val': 5.00001
}},
       'ka_br_lvl3': {'type': KaBrLevel3, 'attr' : {}},
       'ka_br_lvl2': {'type': KaBrLevel2, 'attr' : {}},
       'ka_br_lvl1': {'type': KaBrLevel1, 'attr' : {}}}#'pareto_sorter': 'dci', 'total_pf_size': 200,'pareto_sorter':'dci', 'dci_div':full_div}}}

# SFR Optimization

This example seeks to optimize a SFR design utilizing the blackboard framework.
We start first by taking a look at the SFR design data using the `h5` add `reactor` interfaces built into `FRDIGe` [cite].
For this we'll examine the objectives that will drive the optimization process: cycle length, plutonium mass, reactivity swing, and core average burnup.
Upon examination, we note that we have removed a significant portion of the design space by ensuring that the reactor design has a cycle length greater than 0 days.

# 2D SFR Optimization

Optimization where we attempt to minimize the reactivity swing, while trying to maximize the burnup.
For this problem, we set no constraints on either objective.

In [ ]:
objectives = {'reactivity swing':   {'ll':0,  'ul':1500, 'goal':'lt', 'variable type': float},
              'burnup':             {'ll':0,   'ul':150,  'goal':'gt', 'variable type': float}}
constraints = {'excess reactivity': {'ll': 0, 'ul': 30000, 'variable type': float}}
bb = {'name': 'bb_opt', 'type': bb_opt.BbOpt, 'attr': {'archive_name': '2d_sa_dci2.h5', 
                                                       'convergence_interval': 25,
                                                       'convergence_type': 'function evals',
                                                       'function_evals': 25000,
                                                       'pf size': 200}}

with open('./sm_gpr_120days_no_pu.pkl', 'rb') as pickle_file:
    sm_ga = pickle.load(pickle_file)
    
problem = SFRProblem(design_variables=design_variables,
                     objectives=objectives,
                     constraints=constraints,
                     sm_type='gpr',
                     sm=sm_ga) 
for x in range(0,1):
    bb_controller = controller.Controller()
    bb_controller.initialize_blackboard(blackboard=bb,
                                  ka=kas_sa, 
                                  agent_wait_time=10,
                                  plot_progress=False,
                                  random_seed=None,
                                  problem=problem)     
    bb = bb_controller.bb_opt
    ka = bb.get_attr('_proxy_server')
    for ka_ in kas_sa.keys():
        ka_ = ka.proxy(ka_)
        ka_.set_attr(_design_accuracy=5)
        ka_.set_attr(_objective_accuracy=5)
        ka_.set_attr(learning_factor=0.25)
        ka_.set_attr(debug_wait=True)
        ka_.set_attr(debug_wait_time=0.05)
    
#    bb_controller.run_single_agent_bb()
    bb_controller.run_multi_agent_bb('bb_opt')
    print(bb.get_attr('abstract_lvls')['level 100']['final'])
    print(len(bb.get_attr('abstract_lvls')['level 1']))
#    shutil.move('2d_sa_{}.h5'.format(x), 'sa_2d_pymoo_5000/2d_sa_{}.h5'.format(x))

    bb_controller.shutdown()
    time.sleep(2)

# 3D SFR Optimization

Optimization where we attempt to minimize the reactivity swing and total plutonium mass, while trying to maximize the burnup.
We set constraints on the max linear heat generation rate, excess reactivity, void coefficient, and Doppler coefficient,

In [4]:
objectives = {'reactivity swing':   {'ll':250,    'ul':1500, 'goal':'lt', 'variable type': float},
              'burnup':             {'ll':50,     'ul':150,  'goal':'gt', 'variable type': float},
              'pu mass':            {'ll':0.0,    'ul':1000, 'goal': 'lt', 'variable type': float}}
constraints = {'max lhgr':          {'ll':0.0,    'ul':45.0,   'variable type': float},
               'excess reactivity': {'ll':1000.0, 'ul':10000.0, 'variable type': float},
               'void':              {'ll':-200.0, 'ul':0.0,    'variable type': float},
               'doppler':           {'ll':-1.0,   'ul':0.0,    'variable type': float}}

bb_ = {'name': 'bb_opt', 'type': bb_opt.BbOpt, 'attr': {'archive_name': '3d_sa.h5', 
                                                       'convergence_interval': 10,
                                                       'convergence_type': 'function evals',
                                                       'function_evals': 5000,
                                                       'pf size': 200}}

with open('./sm_gpr_120days_no_pu.pkl', 'rb') as pickle_file:
    sm_ga = pickle.load(pickle_file)
    
problem = SFRProblem(design_variables=design_variables,
                     objectives=objectives,
                     constraints=constraints,
                     sm_type='gpr',
                     sm=sm_ga) 
for x in range(0,1):
    bb_controller = controller.Controller()
    bb_controller.initialize_blackboard(blackboard=bb_,
                                  ka=kas_sa, 
                                  agent_wait_time=10,
                                  plot_progress=False,
                                  random_seed=None,
                                  problem=problem)     
    bb = bb_controller.bb_opt

#    bb.set_attr(_DEBUG=True)
    ka = bb.get_attr('_proxy_server')
    for ka_ in kas_sa.keys():
        ka_ = ka.proxy(ka_)
        ka_.set_attr(_design_accuracy=6)
        ka_.set_attr(_objective_accuracy=6)
        ka_.set_attr(learning_factor=0.25)      
#        ka_.set_attr(debug_wait=True)
#        ka_.set_attr(debug_wait_time=0.05)
    
    bb_controller.run_single_agent_bb('bb_opt')
#    bb_controller.run_multi_agent_bb('bb_opt')
    print(bb.get_attr('abstract_lvls')['level 100']['final'])
    print(len(bb.get_attr('abstract_lvls')['level 1']))
    print(len(bb.get_attr('abstract_lvls')['level 3']['old']))
    shutil.move('3d_sa.h5', 'sa_3d_2/3d_sa_{}.h5'.format(x))    
    bb_controller.shutdown()
    time.sleep(2)

Broadcast server running on 0.0.0.0:9091
NS running on 127.0.0.1:12271 (127.0.0.1)
URI = PYRO:Pyro.NameServer@127.0.0.1:12271
INFO [2021-02-23 16:45:50.390836] (bb_opt): Connected agent ka_rp_explore of agent type <class 'src.ka.ka_s.stochastic.Stochastic'>
INFO [2021-02-23 16:45:50.701886] (bb_opt): Connected agent ka_rp_lhc of agent type <class 'src.ka.ka_s.latin_hypercube.LatinHypercube'>
INFO [2021-02-23 16:45:51.122922] (bb_opt): Connected agent ka_rp_hc of agent type <class 'src.ka.ka_s.hill_climb.HillClimb'>
INFO [2021-02-23 16:45:51.312755] (bb_opt): Connected agent ka_rp_pert of agent type <class 'src.ka.ka_s.neighborhood_search.NeighborhoodSearch'>
INFO [2021-02-23 16:45:51.499037] (bb_opt): Connected agent ka_rp_ga of agent type <class 'src.ka.ka_s.genetic_algorithm.GeneticAlgorithm'>
INFO [2021-02-23 16:45:51.689822] (bb_opt): Connected agent ka_rp_pymoo of agent type <class 'src.ka.ka_s.pymoo_plugin.PyMooAlgorithm'>
INFO [2021-02-23 16:45:51.874447] (bb_opt): Connected age

{'height': 56.15061, 'smear': 79.116115, 'pu_content': 0.036198}
{'height': 55.017841, 'smear': 79.116115, 'pu_content': 0.036869}
{'height': 56.037333, 'smear': 79.116115, 'pu_content': 0.036198}
{'height': 55.017841, 'smear': 79.116115, 'pu_content': 0.036802}
{'height': 55.935384, 'smear': 79.116115, 'pu_content': 0.036198}
{'height': 55.017841, 'smear': 79.116115, 'pu_content': 0.036741}
{'height': 55.843629, 'smear': 79.116115, 'pu_content': 0.036198}
{'height': 55.017841, 'smear': 79.116115, 'pu_content': 0.036687}
{'height': 55.76105, 'smear': 79.116115, 'pu_content': 0.036198}
{'height': 55.017841, 'smear': 79.116115, 'pu_content': 0.036638}
{'height': 55.68673, 'smear': 79.116115, 'pu_content': 0.036198}
{'height': 55.017841, 'smear': 79.116115, 'pu_content': 0.036594}
{'height': 55.017841, 'smear': 79.981796, 'pu_content': 0.036198}
{'height': 55.619841, 'smear': 79.116115, 'pu_content': 0.036198}
{'height': 55.017841, 'smear': 79.116115, 'pu_content': 0.036554}
{'height': 55

{'height': 55.7212786826258, 'smear': 79.116115, 'pu_content': 0.10167}
{'height': 54.56634530332326, 'smear': 79.116115, 'pu_content': 0.08040182732716265}
{'height': 55.017841, 'smear': 79.11829675321094, 'pu_content': 0.07455655591349511}
{'height': 55.017841, 'smear': 79.53180120822067, 'pu_content': 0.03600669876077022}
{'height': 57.07477471883271, 'smear': 79.116115, 'pu_content': 0.036107485570256496}
{'height': 57.71380200586794, 'smear': 79.116115, 'pu_content': 0.036198}
{'height': 56.16423262533914, 'smear': 79.116115, 'pu_content': 0.036198}
{'height': 59.887978994666575, 'smear': 79.895227, 'pu_content': 0.03620262674665902}
{'height': 77.72562368280214, 'smear': 79.22799966773916, 'pu_content': 0.2580626367518739}
{'height': 55.02429177407713, 'smear': 79.116115, 'pu_content': 0.03600437325334097}
{'height': 99.19306357477573, 'smear': 79.81200805363058, 'pu_content': 0.2769910760866259}
{'height': 65.05959795445274, 'smear': 63.31913788203599, 'pu_content': 0.2642708860

{'height': 70.5402868892154, 'smear': 57.129575, 'pu_content': 0.6293811625579045}
{'height': 65.98761078816464, 'smear': 58.399972763840246, 'pu_content': 0.635965754577466}
{'height': 62.71093809722804, 'smear': 62.52418878371703, 'pu_content': 0.6603500832801243}
{'height': 53.633588, 'smear': 65.23877136990463, 'pu_content': 0.71713}
{'height': 76.86268729206854, 'smear': 79.11533988701848, 'pu_content': 0.3396047507423752}
{'height': 61.48121456337261, 'smear': 65.02691568745888, 'pu_content': 0.023668144721531836}
{'height': 61.610738833157875, 'smear': 79.77915859451308, 'pu_content': 0.3396047507423752}
{'height': 53.02391166476775, 'smear': 67.50272161729052, 'pu_content': 0.7202335586028961}
{'height': 57.941715, 'smear': 77.75385659250608, 'pu_content': 0.027963386824995832}
{'height': 63.950485328148424, 'smear': 63.140267917968565, 'pu_content': 0.3317244904959828}
{'height': 61.83036595610457, 'smear': 61.64185256552048, 'pu_content': 0.6603500832801243}
{'height': 72.844

{'height': 58.11175554400205, 'smear': 69.48878963769039, 'pu_content': 0.010891717452743921}
{'height': 93.33828695755878, 'smear': 65.85418458486615, 'pu_content': 0.16760901643175635}
{'height': 59.474286, 'smear': 79.7282145038458, 'pu_content': 0.26336486063578973}
{'height': 61.557544956495235, 'smear': 60.820901069657715, 'pu_content': 0.448637}
{'height': 55.59351652585217, 'smear': 77.79469621727883, 'pu_content': 0.09703151080143663}
{'height': 96.14863944413648, 'smear': 77.95813049204337, 'pu_content': 0.04765661777880581}
{'height': 99.05639514270146, 'smear': 79.30686044352314, 'pu_content': 0.273427}
{'height': 66.02605571440208, 'smear': 62.51661667982981, 'pu_content': 0.70682800249335}
{'height': 83.16585898811381, 'smear': 76.7469128903967, 'pu_content': 0.1438234184838664}
{'height': 62.93057856152442, 'smear': 79.91471229899872, 'pu_content': 0.12375780903746778}
{'height': 63.55493174845848, 'smear': 61.41840469476233, 'pu_content': 0.6603500832801243}
{'height': 

...

{'height': 59.042467, 'smear': 79.91784713108088, 'pu_content': 6e-06}
{'height': 58.237132, 'smear': 79.82884687375888, 'pu_content': 0.01255}
{'height': 75.18058442609929, 'smear': 78.7733652692575, 'pu_content': 0.0017355414271178048}
{'height': 70.94873634355835, 'smear': 77.7974960787435, 'pu_content': 6.2e-05}
{'height': 76.36307287442193, 'smear': 79.5966844233294, 'pu_content': 0.017803}
{'height': 76.36307287442193, 'smear': 79.5966844233294, 'pu_content': 0.02176}
{'height': 68.726766, 'smear': 79.5966844233294, 'pu_content': 0.01978148020104578}
{'height': 76.36307287442193, 'smear': 79.5966844233294, 'pu_content': 0.016023}
{'height': 76.36307287442193, 'smear': 79.5966844233294, 'pu_content': 0.019583}
{'height': 68.726766, 'smear': 79.5966844233294, 'pu_content': 0.017803}
{'height': 76.36307287442193, 'smear': 79.5966844233294, 'pu_content': 0.014421}
{'height': 76.36307287442193, 'smear': 79.5966844233294, 'pu_content': 0.017625}
{'height': 68.726766, 'smear': 79.596684

{'height': 74.428779, 'smear': 78.7733652692575, 'pu_content': 0.000298}
{'height': 67.662526, 'smear': 78.7733652692575, 'pu_content': 0.000241}
{'height': 67.662526, 'smear': 78.7733652692575, 'pu_content': 0.000295}
{'height': 60.896273, 'smear': 78.7733652692575, 'pu_content': 0.000268}
{'height': 74.428779, 'smear': 78.7733652692575, 'pu_content': 0.000268}
{'height': 67.662526, 'smear': 78.7733652692575, 'pu_content': 0.000217}
{'height': 67.662526, 'smear': 78.7733652692575, 'pu_content': 0.000265}
{'height': 60.896273, 'smear': 78.7733652692575, 'pu_content': 0.000241}
{'height': 74.428779, 'smear': 78.7733652692575, 'pu_content': 0.000241}
{'height': 67.662526, 'smear': 78.7733652692575, 'pu_content': 0.000195}
{'height': 67.662526, 'smear': 78.7733652692575, 'pu_content': 0.000239}
{'height': 60.896273, 'smear': 78.7733652692575, 'pu_content': 0.000217}
{'height': 74.428779, 'smear': 78.7733652692575, 'pu_content': 0.000217}
{'height': 67.662526, 'smear': 78.7733652692575, 'p

{'height': 76.36307287442193, 'smear': 79.5966844233294, 'pu_content': 0.000268}
{'height': 74.428779, 'smear': 78.7733652692575, 'pu_content': 0.004525}
{'height': 76.07029153597854, 'smear': 79.29635251169113, 'pu_content': 0.000225}
{'height': 63.827577, 'smear': 79.21875757020263, 'pu_content': 0.02992282709730649}
{'height': 65.67092271082096, 'smear': 78.7733652692575, 'pu_content': 0.000631}
{'height': 63.14614, 'smear': 79.82884687375888, 'pu_content': 0.012864}
{'height': 63.827577, 'smear': 78.7733652692575, 'pu_content': 0.000218}
{'height': 75.18058442609929, 'smear': 79.29635251169113, 'pu_content': 0.000245}
{'height': 68.726766, 'smear': 78.7733652692575, 'pu_content': 0.000105}
{'height': 67.662526, 'smear': 79.5966844233294, 'pu_content': 0.012979}
{'height': 77.49319715937428, 'smear': 73.150223, 'pu_content': 0.00146}
{'height': 56.637521, 'smear': 79.91784713108088, 'pu_content': 0.011934521731587738}
{'height': 57.193567, 'smear': 79.91784713108088, 'pu_content': 1

{'height': 59.042467, 'smear': 79.91784713108088, 'pu_content': 0.02992282709730649}
{'height': 71.49275525716558, 'smear': 79.50441138594105, 'pu_content': 6e-06}
{'height': 62.301273, 'smear': 79.91784713108088, 'pu_content': 0.036198}
{'height': 64.32006578922535, 'smear': 79.82884687375888, 'pu_content': 0.012164}
{'height': 60.54804988742906, 'smear': 79.29635251169113, 'pu_content': 0.0026611938911623167}
{'height': 64.61277879077177, 'smear': 76.90786973441352, 'pu_content': 0.00048381108196958266}
{'height': 67.662526, 'smear': 78.7733652692575, 'pu_content': 0.003266}
{'height': 76.36307287442193, 'smear': 79.5966844233294, 'pu_content': 0.000192}
{'height': 67.662526, 'smear': 79.29635251169113, 'pu_content': 0.000205}
{'height': 59.469397, 'smear': 79.91784713108088, 'pu_content': 1.1e-05}
{'height': 56.202474, 'smear': 79.91784713108088, 'pu_content': 0.000489}
{'height': 56.637521, 'smear': 79.91784713108088, 'pu_content': 0.000169}
{'height': 60.94759183917073, 'smear': 7

KeyboardInterrupt: 

# Plutonium Disposition

In [4]:
objectives = {'pu ratio':           {'ll':0.70,   'ul':0.90,    'goal': 'lt', 'variable type': float},
              'pu disposed':        {'ll':0.0,    'ul':50.0,    'goal': 'gt', 'variable type': float},
              'burnup':             {'ll':50.0,   'ul':150.0,   'goal': 'et', 'target': 100.0, 'variable type': float}}
constraints = {'reactivity swing':  {'ll':250.0,  'ul':1500.0,  'variable type': float},
               'max lhgr':          {'ll':0.0,    'ul':45.0,    'variable type': float},
               'pu240 ratio':       {'ll':0.1,    'ul':1.0,     'variable type': float},
               'excess reactivity': {'ll':1000.0, 'ul':10000.0, 'variable type': float},
               'void':              {'ll':-200.0, 'ul':0.0,     'variable type': float},
               'doppler':           {'ll':-1.0,   'ul':0.0,     'variable type': float},
               'pu mass':           {'ll':0.0,    'ul':1E10,    'variable type': float}}


bb = {'name': 'bb_opt', 'type': bb_opt.BbOpt, 'attr': {'archive_name': 'pu_sa_pu_mass.h5', 
                                                       'convergence_interval': 25,
                                                       'convergence_type': 'function evals',
                                                       'function_evals': 25000,
                                                       'pf size': 200}}

with open('./sm_ann_240days_pu.pkl', 'rb') as pickle_file:
    sm_ga = pickle.load(pickle_file)
    
problem = SFRProblem(design_variables=design_variables,
                     objectives=objectives,
                     constraints=constraints,
                     sm_type='ann',
                     sm=sm_ga) 
for x in range(1,2):
    bb_controller = controller.Controller()
    bb_controller.initialize_blackboard(blackboard=bb,
                                  ka=kas_sa, 
                                  agent_wait_time=10,
                                  plot_progress=False,
                                  random_seed=None,
                                  problem=problem)     
    bb = bb_controller.bb_opt

#    bb.set_attr(_DEBUG=True)
    ka = bb.get_attr('_proxy_server')
    for ka_ in kas_sa.keys():
        ka_ = ka.proxy(ka_)
        ka_.set_attr(_design_accuracy=5)
        ka_.set_attr(_objective_accuracy=5)
        ka_.set_attr(debug_wait=True)
        ka_.set_attr(debug_wait_time=0.1)
    
#    bb_controller.run_single_agent_bb()
    bb_controller.run_multi_agent_bb('bb_opt')
    print(bb.get_attr('abstract_lvls')['level 100']['final'])
    print(len(bb.get_attr('abstract_lvls')['level 1']))
#    shutil.move('pu_sa_{}.h5'.format(x), 'sa_pu/pu_sa_{}.h5'.format(x))    
    bb_controller.shutdown()
    time.sleep(2)

Broadcast server running on 0.0.0.0:9091
NS running on 127.0.0.1:17787 (127.0.0.1)
URI = PYRO:Pyro.NameServer@127.0.0.1:17787
INFO [2021-02-22 14:09:57.504567] (bb_opt): Connected agent ka_rp_explore of agent type <class 'src.ka.ka_s.stochastic.Stochastic'>
INFO [2021-02-22 14:09:57.819851] (bb_opt): Connected agent ka_rp_lhc of agent type <class 'src.ka.ka_s.latin_hypercube.LatinHypercube'>
INFO [2021-02-22 14:09:58.254983] (bb_opt): Connected agent ka_rp_hc of agent type <class 'src.ka.ka_s.hill_climb.HillClimb'>
INFO [2021-02-22 14:09:58.454364] (bb_opt): Connected agent ka_rp_pert of agent type <class 'src.ka.ka_s.neighborhood_search.NeighborhoodSearch'>
INFO [2021-02-22 14:09:58.668820] (bb_opt): Connected agent ka_rp_ga of agent type <class 'src.ka.ka_s.genetic_algorithm.GeneticAlgorithm'>
INFO [2021-02-22 14:09:58.886605] (bb_opt): Connected agent ka_rp_pymoo of agent type <class 'src.ka.ka_s.pymoo_plugin.PyMooAlgorithm'>
INFO [2021-02-22 14:09:59.088452] (bb_opt): Connected age

INFO [2021-02-22 14:10:05.808154] (bb_opt): Selecting agent ka_rp_explore (TV: 3.25) to execute (TE: 68)
INFO [2021-02-22 14:10:05.884608] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 69)
INFO [2021-02-22 14:10:05.957900] (bb_opt): Selecting agent ka_br_lvl2 (TV: 4.0) to execute (TE: 70)
INFO [2021-02-22 14:10:06.030305] (bb_opt): Selecting agent ka_br_lvl1 (TV: 6.0) to execute (TE: 71)
INFO [2021-02-22 14:10:06.104206] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 72)
INFO [2021-02-22 14:10:06.178846] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 73)
INFO [2021-02-22 14:10:06.253018] (bb_opt): Selecting agent ka_br_lvl2 (TV: 4.0) to execute (TE: 74)
INFO [2021-02-22 14:10:06.329674] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 75)
INFO [2021-02-22 14:10:06.768435] (bb_opt): Problem is at 159 of 25000 total allowable function evals
INFO [2021-02-22 14:10:06.840677] (bb_opt): Selecting agent ka_br_lvl2 (TV: 4.0) to ex

INFO [2021-02-22 14:10:14.474536] (bb_opt): Selecting agent ka_br_lvl1 (TV: 6.0) to execute (TE: 146)
INFO [2021-02-22 14:10:14.555429] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 147)
INFO [2021-02-22 14:10:14.649674] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 148)
INFO [2021-02-22 14:10:14.840253] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 149)
INFO [2021-02-22 14:10:14.933196] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 150)
INFO [2021-02-22 14:10:15.032403] (bb_opt): Problem is at 356 of 25000 total allowable function evals
INFO [2021-02-22 14:10:15.175344] (bb_opt): Selecting agent ka_br_lvl2 (TV: 4.0) to execute (TE: 151)
INFO [2021-02-22 14:10:15.304554] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 152)
INFO [2021-02-22 14:10:15.483386] (bb_opt): Selecting agent ka_br_lvl2 (TV: 4.0) to execute (TE: 153)
INFO [2021-02-22 14:10:15.617073] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) t

INFO [2021-02-22 14:10:25.731660] (bb_opt): Selecting agent ka_br_lvl2 (TV: 4.0) to execute (TE: 224)
INFO [2021-02-22 14:10:25.880065] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 225)
INFO [2021-02-22 14:10:25.953475] (bb_opt): Problem is at 542 of 25000 total allowable function evals
INFO [2021-02-22 14:10:26.100504] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 226)
INFO [2021-02-22 14:10:26.234207] (bb_opt): Selecting agent ka_br_lvl2 (TV: 4.0) to execute (TE: 227)
INFO [2021-02-22 14:10:26.371948] (bb_opt): Selecting agent ka_rp_explore (TV: 3.25) to execute (TE: 228)
INFO [2021-02-22 14:10:26.511452] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 229)
INFO [2021-02-22 14:10:26.604192] (bb_opt): Selecting agent ka_br_lvl2 (TV: 4.0) to execute (TE: 230)
INFO [2021-02-22 14:10:26.827485] (bb_opt): Selecting agent ka_br_lvl1 (TV: 6.0) to execute (TE: 231)
INFO [2021-02-22 14:10:26.969026] (bb_opt): Selecting agent ka_rp_pert (TV: 5.

INFO [2021-02-22 14:10:38.913123] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 301)
INFO [2021-02-22 14:10:39.139353] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 302)
INFO [2021-02-22 14:10:39.299598] (bb_opt): Selecting agent ka_br_lvl2 (TV: 4.0) to execute (TE: 303)
INFO [2021-02-22 14:10:39.468989] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 304)
INFO [2021-02-22 14:10:39.683890] (bb_opt): Selecting agent ka_br_lvl2 (TV: 4.0) to execute (TE: 305)
INFO [2021-02-22 14:10:39.868753] (bb_opt): Selecting agent ka_br_lvl1 (TV: 6.0) to execute (TE: 306)
INFO [2021-02-22 14:10:40.022367] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 307)
INFO [2021-02-22 14:10:40.180578] (bb_opt): Selecting agent ka_rp_explore (TV: 3.0) to execute (TE: 308)
INFO [2021-02-22 14:10:40.339525] (bb_opt): Selecting agent ka_br_lvl3 (TV: 3.0) to execute (TE: 309)
INFO [2021-02-22 14:10:40.581399] (bb_opt): Selecting agent ka_br_lvl2 (TV: 4.0

...

INFO [2021-02-22 14:40:14.972739] (bb_opt): Selecting agent ka_br_lvl2 (TV: 14.0) to execute (TE: 2849)
INFO [2021-02-22 14:40:16.403624] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 2850)
INFO [2021-02-22 14:40:17.301486] (bb_opt): Problem is at 22112 of 25000 total allowable function evals
INFO [2021-02-22 14:40:18.441759] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 2851)
INFO [2021-02-22 14:40:19.867061] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 2852)
INFO [2021-02-22 14:40:21.261973] (bb_opt): Selecting agent ka_br_lvl3 (TV: 5.48) to execute (TE: 2853)
INFO [2021-02-22 14:40:22.962253] (bb_opt): Selecting agent ka_br_lvl2 (TV: 10.4) to execute (TE: 2854)
INFO [2021-02-22 14:40:23.568486] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 2855)
INFO [2021-02-22 14:40:25.110577] (bb_opt): Selecting agent ka_rp_explore (TV: 4.5) to execute (TE: 2856)
INFO [2021-02-22 14:40:25.752539] (bb_opt): Selecting agent ka_br_

INFO [2021-02-22 14:41:46.707177] (bb_opt): Problem is at 22551 of 25000 total allowable function evals
INFO [2021-02-22 14:41:47.825058] (bb_opt): Selecting agent ka_br_lvl3 (TV: 5.2) to execute (TE: 2926)
INFO [2021-02-22 14:41:49.495777] (bb_opt): Selecting agent ka_br_lvl2 (TV: 12.0) to execute (TE: 2927)
INFO [2021-02-22 14:41:50.110699] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 2928)
INFO [2021-02-22 14:41:51.664073] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 2929)
INFO [2021-02-22 14:41:52.294177] (bb_opt): Selecting agent ka_br_lvl2 (TV: 9.6) to execute (TE: 2930)
INFO [2021-02-22 14:41:52.987059] (bb_opt): Selecting agent ka_br_lvl3 (TV: 5.08) to execute (TE: 2931)
INFO [2021-02-22 14:41:54.731639] (bb_opt): Selecting agent ka_br_lvl2 (TV: 11.6) to execute (TE: 2932)
INFO [2021-02-22 14:41:56.148567] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 2933)
INFO [2021-02-22 14:41:57.560045] (bb_opt): Selecting agent ka_rp_per

INFO [2021-02-22 14:43:30.797299] (bb_opt): Selecting agent ka_br_lvl2 (TV: 8.0) to execute (TE: 3002)
INFO [2021-02-22 14:43:31.431707] (bb_opt): Selecting agent ka_rp_hc (TV: 5.0) to execute (TE: 3003)
INFO [2021-02-22 14:43:33.293820] (bb_opt): Selecting agent ka_br_lvl2 (TV: 13.6) to execute (TE: 3004)
INFO [2021-02-22 14:43:34.898758] (bb_opt): Selecting agent ka_rp_hc (TV: 5.0) to execute (TE: 3005)
INFO [2021-02-22 14:43:36.334709] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 3006)
INFO [2021-02-22 14:43:37.893993] (bb_opt): Selecting agent ka_rp_explore (TV: 5.0) to execute (TE: 3007)
INFO [2021-02-22 14:43:39.387086] (bb_opt): Selecting agent ka_br_lvl3 (TV: 5.28) to execute (TE: 3008)
INFO [2021-02-22 14:43:41.534691] (bb_opt): Selecting agent ka_br_lvl2 (TV: 6.4) to execute (TE: 3009)
INFO [2021-02-22 14:43:43.118213] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 3010)
INFO [2021-02-22 14:43:43.770203] (bb_opt): Selecting agent ka_br_lvl3 (

INFO [2021-02-22 14:45:25.538298] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 3079)
INFO [2021-02-22 14:45:26.185808] (bb_opt): Selecting agent ka_br_lvl3 (TV: 4.16) to execute (TE: 3080)
INFO [2021-02-22 14:45:27.957959] (bb_opt): Selecting agent ka_br_lvl2 (TV: 8.4) to execute (TE: 3081)
INFO [2021-02-22 14:45:29.703468] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 3082)
INFO [2021-02-22 14:45:30.388320] (bb_opt): Selecting agent ka_rp_hc (TV: 5.0) to execute (TE: 3083)
INFO [2021-02-22 14:45:31.147963] (bb_opt): Selecting agent ka_rp_hc (TV: 5.0) to execute (TE: 3084)
INFO [2021-02-22 14:45:32.784687] (bb_opt): Selecting agent ka_rp_pert (TV: 5.0) to execute (TE: 3085)
INFO [2021-02-22 14:45:34.311990] (bb_opt): Selecting agent ka_br_lvl3 (TV: 5.12) to execute (TE: 3086)
INFO [2021-02-22 14:45:36.291882] (bb_opt): Selecting agent ka_rp_explore (TV: 5.25) to execute (TE: 3087)
INFO [2021-02-22 14:45:37.851509] (bb_opt): Selecting agent ka_br_lvl2 

INFO [2021-02-22 14:58:27.749019] (ka_rp_lhc): Agent ka_rp_lhc shutting down
INFO [2021-02-22 14:58:27.752804] (ka_rp_hc): Agent ka_rp_hc shutting down
INFO [2021-02-22 14:58:27.756259] (ka_rp_pert): Agent ka_rp_pert shutting down
INFO [2021-02-22 14:58:27.759866] (ka_rp_ga): Agent ka_rp_ga shutting down
INFO [2021-02-22 14:58:28.014890] (ka_br_lvl3): Agent ka_br_lvl3 shutting down
INFO [2021-02-22 14:58:28.022232] (ka_br_lvl2): Agent ka_br_lvl2 shutting down
INFO [2021-02-22 14:58:28.027847] (ka_br_lvl1): Agent ka_br_lvl1 shutting down
INFO [2021-02-22 14:58:28.098534] (ka_rp_pymoo): Agent ka_rp_pymoo shutting down
{'agent': 'final', 'time': 2908.5182468891144, 'hvi': 0.0}
910
NS shut down.


In [ ]:
ns = run_nameserver()
bb = run_agent(name='bb', base=bb_opt.BbOpt)
bb.set_attr(archive_name='sfr_bb_base_3d.h5')
bb.load_h5(panels={2:['new','old'],3:['new','old']})
lvl2 = []
lvl3 = []
lvl1 = []
mc = []
hc = []
ga = []
pert = []
print(len(bb.get_attr('abstract_lvls')['level 1']))
print(bb.get_attr('abstract_lvls')['level 100']['final'])
for trigger in bb.get_attr('abstract_lvls')['level 100'].values():
    if 'lvl3' in trigger['agent']:
        lvl3.append(trigger['time'])
    elif 'lvl2' in trigger['agent']:
        lvl2.append(trigger['time'])
    elif 'lvl1' in trigger['agent']:
        lvl1.append(trigger['time'])
    elif 'mc' in trigger['agent']:
        mc.append(trigger['time'])
    elif 'hc' in trigger['agent']:
        hc.append(trigger['time'])
    elif 'ga' in trigger['agent']:
        ga.append(trigger['time'])
    elif 'pert' in trigger['agent']:
        pert.append(trigger['time'])
        
#dict_ = {'lvl3': }
#df = pd.DataFrame(list(zip(lvl3, lvl2, lvl1)), columns=['time', 'time', 'lvl1'])
#print(df)
#fig1 = px.line(df, y='time',
#                  labels={'x':'times triggered', 'y': 'time'})
#fig1.show()
fig = go.Figure()
for level in [(lvl3, 'level 3'), (lvl2, 'level 2'), (lvl1, 'level 1')]:#, mc, hc, ga, pert]:
    fig.add_trace(go.Scatter(x=[i for i in range(len(level[0]))], y=level[0], name=level[1]))

fig.update_layout(xaxis_title='Times Triggered',
                  yaxis_title='Time (s)')
fig.show()

fig = go.Figure()
for level in [(mc, 'MC'), (hc, 'HC'), (ga, 'GA'), (pert, 'Pert')]:#, mc, hc, ga, pert]:
    fig.add_trace(go.Scatter(x=[i for i in range(len(level[0]))], y=level[0], name=level[1]))

fig.update_layout(xaxis_title='Times Triggered',
                  yaxis_title='Time (s)')
fig.show()

# Multi Tiered Controller

In [ ]:
    mtc = controller.Multi_Tiered_Controller()
    kas = {'mka_rp_mc': Stochastic,
           'mka_rp_hc': HillClimb,
           'mka_rp_pert': NeighborhoodSearch,
           'mka_br_lvl3': KaBrLevel3,
           'mka_br_lvl2': KaBrLevel2,
           'mka_br_lvl1': KaBrLevel1}
    
    mtc.initialize_blackboard('master_bb', bb_name='bb_master', bb_type=bb_opt.MasterBbOpt, ka=kas, archive='bb_master', convergence_model={'type': 'hvi', 'convergence rate': 0.5, 'interval': 5, 'pf size': 5, 'total tvs': 50}, random_seed=1)
    
    master_bb = mtc.master_bb
    kas = {'ska_rp_mc': Stochastic, 
           'ska_rp_hc': HillClimb,
           'ska_rp_pert': NeighborhoodSearch,
           'ska_br_lvl3': KaBrLevel3,
           'ska_br_lvl2': KaBrLevel2,
           'ska_br_lvl1': KaBrLevel1,
           'ska_br_inter': kabr.KaBr_interBB}
        
    mtc.initialize_blackboard('sub_bb', bb_name='bb_sub', bb_type=bb_opt.SubBbOpt, ka=kas,  archive='bb_sub', convergence_model={'type': 'hvi', 'convergence rate': 0.5, 'interval': 5, 'pf size': 5, 'total tvs': 50}, random_seed=1)
    sub_bb = mtc.sub_bb    
    mtc.run_sub_bb(sub_bb)
 #   master_bb.set_attr(_DEBUG=True)
    mtc.run_sub_bb(master_bb)

    os.remove('bb_sub.h5')
    os.remove('bb_master.h5')
    assert master_bb.get_attr('_kaar') == {1: {'mka_rp_mc': 0.250001, 'mka_rp_hc': 0, 'mka_rp_pert': 0, 'mka_br_lvl3': 3.00000000001, 'mka_br_lvl2': 0, 'mka_br_lvl1': 0}, 2: {'mka_br_lvl3': 0, 'mka_br_lvl1': 0, 'mka_rp_mc': 0.500002, 'mka_rp_hc': 0, 'mka_rp_pert': 0, 'mka_br_lvl2': 4.00000000002}, 3: {'mka_br_lvl3': 0, 'mka_br_lvl2': 0, 'mka_br_lvl1': 0, 'mka_rp_mc': 0.750003, 'mka_rp_hc': 5.00001, 'mka_rp_pert': 5.00001}, 4: {'mka_br_lvl3': 3.00000000001, 'mka_br_lvl2': 0, 'mka_br_lvl1': 0, 'mka_rp_mc': 1.000004, 'mka_rp_hc': 5.00001, 'mka_rp_pert': 0}, 5: {'mka_rp_mc': 1.2500049999999998, 'mka_rp_hc': 0, 'mka_rp_pert': 0, 'mka_br_lvl1': 0, 'mka_br_lvl3': 7.00000000001, 'mka_br_lvl2': 0}, 6: {'mka_br_lvl3': 0, 'mka_br_lvl1': 0, 'mka_rp_mc': 1.5000059999999997, 'mka_rp_hc': 0, 'mka_rp_pert': 0, 'mka_br_lvl2': 10.00000000002}, 7: {'mka_rp_mc': 1.7500069999999996, 'mka_rp_hc': 5.00001, 'mka_rp_pert': 5.00001, 'mka_br_lvl3': 0, 'mka_br_lvl2': 0, 'mka_br_lvl1': 6.00000000003}, 8: {'mka_br_lvl3': 0, 'mka_br_lvl2': 0, 'mka_br_lvl1': 0, 'mka_rp_mc': 2.000008, 'mka_rp_hc': 5.00001, 'mka_rp_pert': 5.00001}, 9: {'mka_br_lvl3': 3.00000000001, 'mka_br_lvl2': 0, 'mka_br_lvl1': 0, 'mka_rp_mc': 2.250009, 'mka_rp_hc': 5.00001, 'mka_rp_pert': 5.00001}, 10: {'mka_rp_pert': 5.00001, 'mka_br_lvl3': 7.00000000001, 'mka_rp_mc': 2.50001, 'mka_rp_hc': 5.00001, 'mka_br_lvl2': 0, 'mka_br_lvl1': 0}}
        
    mtc.shutdown()
    time.sleep(0.05) 

In [ ]:
    kas = {'ka_rp_explore': Stochastic, 
           'ka_rp_exploit': NeighborhoodSearch,
           'ka_br_lvl3': KaBrLevel3,
           'ka_br_lvl2': KaBrLevel2,
           'ka_br_lvl1': KaBrLevel1,}
    objectives = {'reactivity swing': {'ll':0,     'ul':750,  'goal':'lt', 'variable type': float},
                           'burnup':           {'ll':0,     'ul':200,  'goal':'gt', 'variable type': float},
                           'pu mass':          {'ll':0,     'ul':1500, 'goal':'lt', 'variable type': float}}    

    bb_controller = controller.Controller(bb_name='sfr_opt', 
                                          bb_type=bb_opt.BbOpt, 
                                          ka=kas,
                                          objectives=objectives,
                                          archive='sfr_opt', 
                                          agent_wait_time=5,
                                          convergence_model={'type': 'hvi', 
                                                             'convergence rate': 1E-3, 
                                                             'interval':5, 
                                                             'pf size': 5, 
                                                             'total tvs': 100,
                                                             'skipped tvs': 0},
                                          surrogate_model={'sm_type'     : 'gpr', 
                                                           'pickle file' : './sm_gpr.pkl'},
                                          random_seed=10983)
   
    bb_controller.run_single_agent_bb()
    lvls = bb_controller.bb.get_blackboard()